In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "CM-ES_Haut-Nyong_gamb_2009_Q3"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Cameroon / Haut-Nyong / gambiae / 2009 / Q3

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          95
country                                                        Cameroon
admin1_iso                                                        CM-ES
admin1_name                                                        East
admin2_name                                                  Haut-Nyong
taxon                                                           gambiae
year                                                               2009
quarter                                                               3
cohort_label                Cameroon / Haut-Nyong / gambiae / 2009 / Q3
sample_query          cohort_admin2_quarter == 'CM-ES_Haut-Nyong_gam...
latitude                                                          4.341
longitude                                                        13.558
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id    contributor   country location  year  month  \
0   AN0007-C         CM0901778  Nora Besansky  Cameroon    Mayos  2009      9   
1   AN0008-C         CM0901779  Nora Besansky  Cameroon    Mayos  2009      9   
2   AN0009-C         CM0901780  Nora Besansky  Cameroon    Mayos  2009      9   
3   AN0010-C         CM0901782  Nora Besansky  Cameroon    Mayos  2009      9   
4   AN0011-C         CM0901783  Nora Besansky  Cameroon    Mayos  2009      9   
..       ...               ...            ...       ...      ...   ...    ...   
90  AN0217-C         CM0901808  Nora Besansky  Cameroon    Mayos  2009      9   
91  AN0218-C         CM0901809  Nora Besansky  Cameroon    Mayos  2009      9   
92  AN0219-C         CM0901810  Nora Besansky  Cameroon    Mayos  2009      9   
93  AN0220-C         CM0901814  Nora Besansky  Cameroon    Mayos  2009      9   
94  AN0221-C         CM0901818  Nora Besansky  Cameroon    Mayos  2009      9   

    latitude  longitude sex_call  ... admin1_name admin1_iso  admin2_name  \
0      4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
1      4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
2      4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
3      4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
4      4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
..       ...        ...      ...  ...         ...        ...          ...   
90     4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
91     4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
92     4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
93     4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   
94     4.341     13.558        F  ...        East      CM-ES   Haut-Nyong   

      taxon  cohort_admin1_year  cohort_admin1_month cohort_admin1_quarter  \
0   gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
1   gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
2   gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
3   gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
4   gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
..      ...                 ...                  ...                   ...   
90  gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
91  gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
92  gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
93  gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   
94  gambiae     CM-ES_gamb_2009   CM-ES_gamb_2009_09    CM-ES_gamb_2009_Q3   

            cohort_admin2_year            cohort_admin2_month  \
0   CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
1   CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
2   CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
3   CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
4   CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
..                         ...                            ...   
90  CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
91  CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
92  CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
93  CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   
94  CM-ES_Haut-Nyong_gamb_2009  CM-ES_Haut-Nyong_gamb_2009_09   

            cohort_admin2_quarter  
0   CM-ES_Haut-Nyong_gamb_2009_Q3  
1   CM-ES_Haut-Nyong_gamb_2009_Q3  
2   CM-ES_Haut-Nyong_gamb_2009_Q3  
3   CM-ES_Haut-Nyong_gamb_2009_Q3  
4   CM-ES_Haut-Nyong_gamb_2009_Q3  
..                            ...  
90  CM-ES_Haut-Nyong_gamb_2009_Q3  
91  CM-ES_Haut-Nyong_gamb_2009_Q3  
92  CM-ES_Haut-Nyong_gamb_2009_Q3  
93  CM-ES_Haut-Nyong_gamb_2

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2009      9     95

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('September', 'September')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0    Mayos     13.558     4.341

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor   Study   Data release              
Nora Besansky Ag1000G Ag3.0         AG1000G-CM-A

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 95 samples from the 
*gambiae* taxon, collected from 1 locations within the administrative 
division of Haut-Nyong, East, Cameroon. Collections were made in September 2009.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter    pcenter  delta_i  \
0  CM-ES_Haut-Nyong_gamb_2009_Q3    2RL   56.976299   28488150     5411   
1  CM-ES_Haut-Nyong_gamb_2009_Q3    2RL   81.175489   40587745     2977   
2  CM-ES_Haut-Nyong_gamb_2009_Q3    2RL  120.399856   63867845     1638   
3  CM-ES_Haut-Nyong_gamb_2009_Q3    2RL  142.010809   74776036     1535   
4  CM-ES_Haut-Nyong_gamb_2009_Q3    2RL  194.144921  100843092     2171   
0  CM-ES_Haut-Nyong_gamb_2009_Q3    3RL   57.156091   28578046     5693   

   stat_max    gpos_max   ppos_max  focus_gstart  focus_gstop  ...      skew  \
0    0.4404   56.925890   28462945     56.842613    57.182633  ... -0.313065   
1    0.1752   81.734716   40867358     80.868862    81.788744  ... -0.500000   
2    0.4056  119.599149   62266431    120.028933   120.966649  ... -0.305853   
3    0.1070  141.743248   74642255    141.703412   142.164508  ...  0.500000   
4    0.1296  194.105056  100823159    194.109566   194.162599  ...  0.500000   
0    0.4844   57.097970   28548985     57.064820    57.219186  ...  0.266313   

   decay_left  decay_right  baseline           aic           bic       rss  \
0    0.534744     0.825335  0.029810 -16464.299251 -16436.159096  0.677965   
1    1.226510     2.453019  0.039444 -13832.717687 -13805.788432  0.302365   
2    1.483690     2.267173  0.049540  -9974.039135  -9947.383834  2.209407   
3    1.229588     0.614794  0.037124 -19183.425156 -19155.632572  0.085975   
4    0.141421     0.070711  0.022655 -20367.654766 -20339.799973  0.053527   
0    0.365084     0.252381  0.028256 -15088.639350 -15060.997691  0.554762   

   constant_aic  bottom  top  
0 -11052.628103       0    1  
1 -10855.579963       0    1  
2  -8335.344934       0    1  
3 -17648.161579       0    1  
4 -18196.510183       0    1  
0  -9394.896584       0    1  

[6 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[4.341, 13.558], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style